This notebook allows collecting results across multiple pipeline runs. Concatenating across sessions and bin sizes. 
It takes CSVs, then determines the most recent one from the filename. 

There are two major sets of decoded epochs - Laps and Ripples/Replays
There are two sets of marginals for the decoded epochs - the "by epoch" and "by time bin" marginals.
The "by time bin" epochs are a larger granulation, with each epoch consisting of one or more time bin.


```python

# 2024-01-23 - 
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-fet11-01_12-58-54_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-03_12-3-25_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-02_17-46-44_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-02_19-28-0_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-10_12-58-3_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-10_12-25-50_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-09_16-40-54_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-09_22-24-40_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-12_16-53-46_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-09_17-29-30_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-08_14-26-15_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-09_1-22-43_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-07_16-40-19_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-08_21-16-25_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-12_15-55-31_time_bin_size_sweep_results.h5



# found_session_export_paths = [Path(v).resolve() for v in  ["C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0420PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0420PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0645PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0645PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0828PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0828PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# ]]

[
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(ripple_simple_pf_pearson_merged_df)_tbin-0.025.csv",
    "2024-02-17_0210AM-kdiba_vvp01_one_2006-4-09_17-29-30-(laps_simple_pf_pearson_merged_df)_tbin-0.025.csv",
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(laps_weighted_corr_merged_df)_tbin-0.025.csv",
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(ripple_weighted_corr_merged_df)_tbin-0.025.csv",
]

```

In [1]:
%config IPCompleter.use_jedi = False
%pdb off
%load_ext autoreload
%autoreload 3

# required to enable non-blocking interaction:
%gui qt5

import sys
from copy import deepcopy
from typing import Dict, List, Tuple, Optional, Callable, Union, Any
from typing_extensions import TypeAlias
from neuropy.utils.result_context import IdentifyingContext
from nptyping import NDArray
import neuropy.utils.type_aliases as types
from collections import defaultdict

import numpy as np
import pandas as pd
import re
from pathlib import Path
from datetime import datetime

from neuropy.utils.indexing_helpers import PandasHelpers
from pyphocorehelpers.indexing_helpers import partition_df
# Set the maximum number of columns to display
pd.set_option('display.max_columns', 100)

# Plotting
# import pylustrator # customization of figures
import matplotlib
import matplotlib as mpl
import matplotlib.pyplot as plt
_bak_rcParams = mpl.rcParams.copy()

matplotlib.use('Qt5Agg')
# %matplotlib inline
# %matplotlib auto

# Switch to the desired interactivity mode
plt.interactive(True)

# _restore_previous_matplotlib_settings_callback = matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
# _restore_previous_matplotlib_settings_callback = matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
import seaborn as sns

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
template: str = 'plotly_dark' # set plotl template
pio.templates.default = template
from pyphocorehelpers.plotting.media_output_helpers import fig_to_clipboard
from pyphocorehelpers.Filesystem.path_helpers import file_uri_from_path

from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _helper_build_figure, plotly_pre_post_delta_scatter, plot_across_sessions_scatter_results

# from ..PendingNotebookCode import plot_across_sessions_scatter_results, plot_histograms, plot_stacked_histograms
from pyphocorehelpers.Filesystem.path_helpers import find_first_extant_path
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import find_csv_files, find_HDF5_files, find_most_recent_files, process_csv_file, plot_across_sessions_scatter_results, plot_histograms, plot_stacked_histograms
from pyphoplacecellanalysis.General.Pipeline.Stages.ComputationFunctions.MultiContextComputationFunctions.DirectionalPlacefieldGlobalComputationFunctions import DecoderDecodedEpochsResult
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import load_across_sessions_exported_files, _process_and_load_exported_file, _common_cleanup_operations, convert_to_dataframe

debug_print: bool = False

# TODAY_DAY_DATE: str = f"2024-04-09_GL"
TODAY_DAY_DATE: str = f"2024-04-16_APOGEE"

print(f'TODAY_DAY_DATE: {TODAY_DAY_DATE}')

types.session_str: TypeAlias = str # a unique session identifier


known_bad_sessions = [IdentifyingContext(format_name='kdiba',animal='pin01',exper_name='one',session_name='11-02_17-46-44')]
known_bad_session_strs = [str(v.get_description()) for v in known_bad_sessions]
known_bad_session_strs

Automatic pdb calling has been turned OFF
build_module_logger(module_name="Spike3D.pipeline"):
	 Module logger com.PhoHale.Spike3D.pipeline has file logging enabled and will log to EXTERNAL\TESTING\Logging\debug_com.PhoHale.Spike3D.pipeline.log
TODAY_DAY_DATE: 2024-04-16_APOGEE


['kdiba_pin01_one_11-02_17-46-44']

# Definitions
"_new" (as in `all_sessions_new_ripple_df`) adds simple_pearson and a few other measures

In [2]:
## Load across session t_delta CSV, which contains the t_delta for each session:

## INPUTS: known_bad_session_strs,


cuttoff_date = datetime(2024, 4, 14)
# cuttoff_date = None

# t_delta_csv_path = Path(r'C:\Users\pho\repos\Spike3DWorkEnv\Spike3D\output\collected_outputs\2024-01-18_GL_t_split_df.csv').resolve() # Apogee
# t_delta_csv_path = Path('/home/halechr/cloud/turbo/Data/Output/collected_outputs/2024-01-18_GL_t_split_df.csv').resolve() # GL

# collected_outputs_directory = '/home/halechr/FastData/collected_outputs/'
# collected_outputs_directory = r'C:\Users\pho\Desktop\collected_outputs'
# collected_outputs_directory = r'C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs' # APOGEE
# collected_outputs_directory = '/home/halechr/cloud/turbo/Data/Output/collected_outputs' # GL

known_collected_outputs_paths = [Path(v).resolve() for v in [r"K:/scratch/collected_outputs", '/Users/pho/Dropbox (University of Michigan)/MED-DibaLabDropbox/Data/Pho/Outputs/output/collected_outputs', r'C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs',
                                                              '/home/halechr/FastData/collected_outputs/', '/home/halechr/cloud/turbo/Data/Output/collected_outputs']]
collected_outputs_directory = find_first_extant_path(known_collected_outputs_paths)
assert collected_outputs_directory.exists(), f"collected_outputs_directory: {collected_outputs_directory} does not exist! Is the right computer's config commented out above?"
# fullwidth_path_widget(scripts_output_path, file_name_label='Scripts Output Path:')
print(f'collected_outputs_directory: {collected_outputs_directory}')

# Create a 'figures' subfolder if it doesn't exist
figures_folder: Path = collected_outputs_directory.joinpath('figures').resolve()
figures_folder.mkdir(parents=False, exist_ok=True)
assert figures_folder.exists()
print(f'\tfigures_folder: {file_uri_from_path(figures_folder)}')

t_delta_csv_path = collected_outputs_directory.joinpath('2024-01-18_GL_t_split_df.csv').resolve() # GL
assert t_delta_csv_path.exists()

## Find the files:
csv_files = find_csv_files(collected_outputs_directory)
h5_files = find_HDF5_files(collected_outputs_directory)

csv_sessions = find_most_recent_files(found_session_export_paths=csv_files, cuttoff_date=cuttoff_date)
h5_sessions = find_most_recent_files(found_session_export_paths=h5_files)

## The CSV containing the session delta time:
t_delta_df = pd.read_csv(t_delta_csv_path, index_col=0) # Assuming that your CSV file has an index column
# adds `delta_aligned_t_start`, `delta_aligned_t_end` columns
t_delta_df['delta_aligned_t_start'] = t_delta_df['t_start'] - t_delta_df['t_delta']
t_delta_df['delta_aligned_t_end'] = t_delta_df['t_end'] - t_delta_df['t_delta']

# computes `earliest_delta_aligned_t_start`, latest_delta_aligned_t_end
earliest_delta_aligned_t_start: float = np.nanmin(t_delta_df['delta_aligned_t_start'])
latest_delta_aligned_t_end: float = np.nanmax(t_delta_df['delta_aligned_t_end'])
print(f'earliest_delta_aligned_t_start: {earliest_delta_aligned_t_start}, latest_delta_aligned_t_end: {latest_delta_aligned_t_end}')
t_delta_dict = t_delta_df.to_dict(orient='index')
# t_delta_df

# #TODO 2024-03-02 12:12: - [ ] Could add weighted correlation if there is a dataframe for that and it's computed:
_df_raw_variable_names = ['simple_pf_pearson_merged_df', 'weighted_corr_merged_df']
_df_variables_names = ['laps_weighted_corr_merged_df', 'ripple_weighted_corr_merged_df', 'laps_simple_pf_pearson_merged_df', 'ripple_simple_pf_pearson_merged_df']

# # tbin_values_dict = {'laps': self.laps_decoding_time_bin_size, 'ripple': self.ripple_decoding_time_bin_size}
time_col_name_dict = {'laps': 'lap_start_t', 'ripple': 'ripple_start_t'} ## default should be 't_bin_center'

# fold older files:
# {'laps_marginals_df': 'lap_start_t', 'ripple_marginals_df': 'ripple_start_t', 'laps_time_bin_marginals_df':'t_bin_center', 'ripple_time_bin_marginals_df':'t_bin_center'}
    

# csv_sessions
# Extract each of the separate files from the sessions:

# final_sessions: Dict[types.session_str, Dict[str, Path]] = {}

final_sessions_loaded_laps_dict = {}
final_sessions_loaded_ripple_dict = {}
final_sessions_loaded_laps_time_bin_dict = {}
final_sessions_loaded_ripple_time_bin_dict = {}

final_sessions_loaded_simple_pearson_laps_dict = {}
final_sessions_loaded_simple_pearson_ripple_dict = {}

# stupid reudndant but compatible method
final_sessions_loaded_laps_wcorr_dict = {}
final_sessions_loaded_ripple_wcorr_dict = {}

final_sessions_loaded_laps_all_scores_dict = {}
final_sessions_loaded_ripple_all_scores_dict = {}

if cuttoff_date is not None:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items() if ((an_export_datetime >= cuttoff_date) and (session_str not in known_bad_session_strs))}
                                                                                              for session_str, session_dict in csv_sessions.items() }
else:
    # no cutoff recency date:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items() if (session_str not in known_bad_session_strs)}
                                                                                            for session_str, session_dict in csv_sessions.items()}


for session_str, session_dict in final_sessions.items():
    session_name = str(session_str)  # Extract session name from the filename
    if debug_print:
        print(f'processing session_name: {session_name}')
    curr_session_t_delta = t_delta_dict.get(session_name, {}).get('t_delta', None)
    if curr_session_t_delta is None:
        print(f'WARN: curr_session_t_delta is None for session_str = "{session_str}"')

    # Process each file type with its corresponding details
    _process_and_load_exported_file(session_dict, 'laps_marginals_df', final_sessions_loaded_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_marginals_df', final_sessions_loaded_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    _process_and_load_exported_file(session_dict, 'laps_time_bin_marginals_df', final_sessions_loaded_laps_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    _process_and_load_exported_file(session_dict, 'ripple_time_bin_marginals_df', final_sessions_loaded_ripple_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    _process_and_load_exported_file(session_dict, 'laps_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    _process_and_load_exported_file(session_dict, 'laps_weighted_corr_merged_df', final_sessions_loaded_laps_wcorr_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_weighted_corr_merged_df', final_sessions_loaded_ripple_wcorr_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    
    # _process_and_load_exported_file(session_dict, 'laps_all_scores_merged_df', final_sessions_loaded_laps_all_scores_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_all_scores_merged_df', final_sessions_loaded_ripple_all_scores_dict, session_str, curr_session_t_delta, 'ripple_start_t')



## Build across_sessions join dataframes:
all_sessions_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_dict.values()), axis='index', ignore_index=True)
all_sessions_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_dict.values()), axis='index', ignore_index=True)
# Add 'epoch_idx' column for compatibility:
if all_sessions_laps_df is not None:
    all_sessions_laps_df['epoch_idx'] = all_sessions_laps_df['lap_idx']
if all_sessions_ripple_df is not None:
    all_sessions_ripple_df['epoch_idx'] = all_sessions_ripple_df['ripple_idx']

# *_time_bin marginals:
all_sessions_laps_time_bin_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_time_bin_dict.values()), axis='index', ignore_index=True)
all_sessions_ripple_time_bin_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_time_bin_dict.values()), axis='index', ignore_index=True)

# NEW ________________________________________________________________________________________________________________ #
all_sessions_simple_pearson_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_simple_pearson_laps_dict.values()), axis='index', ignore_index=True)
all_sessions_simple_pearson_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_simple_pearson_ripple_dict.values()), axis='index', ignore_index=True)

if len(final_sessions_loaded_laps_wcorr_dict) > 0:
    all_sessions_wcorr_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_wcorr_dict.values()), axis='index', ignore_index=True)
else:
    all_sessions_wcorr_laps_df = None # empty df would be better

all_sessions_wcorr_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_wcorr_dict.values()), axis='index', ignore_index=True)

# `*_all_scores_*`: __________________________________________________________________________________________________ #
# all_sessions_all_score_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_all_scores_dict.values()), axis='index', ignore_index=True)
all_sessions_all_scores_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_all_scores_dict.values()), axis='index', ignore_index=True)


dfs_list = (all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df)
for a_df in dfs_list:
    if a_df is not None:
        if 'time_bin_size' not in a_df:
            print('Uh-oh! time_bin_size is missing! This must be old exports!')
            print(f'\tTry to determine the time_bin_size from the filenames: {csv_sessions}')
            ## manual correction UwU
            time_bin_size: float = 0.025
            print(f'WARNING! MANUAL OVERRIDE TIME BIN SIZE SET: time_bin_size = {time_bin_size}. Assigning to dataframes....')
            a_df['time_bin_size'] = time_bin_size
        else:
            # Filter rows based on column: 'time_bin_size'
            a_df = a_df[a_df['time_bin_size'].notna()]


# if 'time_bin_size' not in all_sessions_laps_df:
#     print('Uh-oh! time_bin_size is missing! This must be old exports!')
#     print(f'\tTry to determine the time_bin_size from the filenames: {csv_sessions}')
#     ## manual correction UwU
#     time_bin_size: float = 0.025
#     print(f'WARNING! MANUAL OVERRIDE TIME BIN SIZE SET: time_bin_size = {time_bin_size}. Assigning to dataframes....')
#     all_sessions_laps_df['time_bin_size'] = time_bin_size
#     all_sessions_ripple_df['time_bin_size'] = time_bin_size
#     all_sessions_laps_time_bin_df['time_bin_size'] = time_bin_size
#     all_sessions_ripple_time_bin_df['time_bin_size'] = time_bin_size
#     print(f'\tdone.')
# else:
#     # Filter rows based on column: 'time_bin_size'
#     all_sessions_laps_df = all_sessions_laps_df[all_sessions_laps_df['time_bin_size'].notna()]
#     all_sessions_ripple_df = all_sessions_ripple_df[all_sessions_ripple_df['time_bin_size'].notna()]
#     all_sessions_laps_time_bin_df = all_sessions_laps_time_bin_df[all_sessions_laps_time_bin_df['time_bin_size'].notna()]
#     all_sessions_ripple_time_bin_df = all_sessions_ripple_time_bin_df[all_sessions_ripple_time_bin_df['time_bin_size'].notna()]

all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df = [_common_cleanup_operations(a_df) for a_df in (all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df)]
all_sessions_simple_pearson_laps_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_laps_df, all_sessions_wcorr_ripple_df = [_common_cleanup_operations(a_df) for a_df in (all_sessions_simple_pearson_laps_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_laps_df, all_sessions_wcorr_ripple_df)]

# all_sessions_all_score_laps_df, all_sessions_all_scores_ripple_df = [_common_cleanup_operations(a_df) for a_df in (all_sessions_all_score_laps_df, all_sessions_all_scores_ripple_df)]
# all_sessions_all_score_laps_df = _common_cleanup_operations(all_sessions_all_score_laps_df)
all_sessions_all_scores_ripple_df = _common_cleanup_operations(all_sessions_all_scores_ripple_df)

all_sessions_simple_pearson_laps_df: pd.DataFrame = DecoderDecodedEpochsResult.merge_decoded_epochs_result_dfs(all_sessions_simple_pearson_laps_df, all_sessions_wcorr_laps_df, should_drop_directional_columns=False, start_t_idx_name='delta_aligned_start_t')
all_sessions_simple_pearson_ripple_df: pd.DataFrame = DecoderDecodedEpochsResult.merge_decoded_epochs_result_dfs(all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_ripple_df, should_drop_directional_columns=False, start_t_idx_name='ripple_start_t')

# all_sessions_laps_time_bin_df # 601845 rows × 9 column

parsed_csv_files_df: pd.DataFrame = convert_to_dataframe(csv_sessions)
parsed_csv_files_df

collected_outputs_directory: K:\scratch\collected_outputs
	figures_folder: file:///K:/scratch/collected_outputs/figures
ERR: Could not parse filename: "session_h5_files_copydict_2024-03-28_Apogee"
ERR: Could not parse filename: "session_h5_files_copydict_2024-04-12_GL"
ERR: Could not parse filename: "session_h5_files_copydict_2024-03-29_GL"
ERR: Could not parse filename: "session_h5_files_copydict_2024-04-15_GL"
ERR: Could not parse date "0000-00-00" of filename: "0000-00-00_Fake-2006-6-07_16-40-19_time_bin_size_sweep_results"
ERR: Could not parse filename: "0000-00-00_Fake-2006-6-07_16-40-19_time_bin_size_sweep_results"
ERR: Could not parse date "0000-00-00" of filename: "0000-00-00_Fake-2006-6-12_15-55-31_time_bin_size_sweep_results"
ERR: Could not parse filename: "0000-00-00_Fake-2006-6-12_15-55-31_time_bin_size_sweep_results"
earliest_delta_aligned_t_start: -2057.2259484970764, latest_delta_aligned_t_end: 1661.8560019930592
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: 

session                           file_type  \
0    kdiba_pin01_one_fet11-01_12-58-54      ripple_weighted_corr_merged_df   
1    kdiba_pin01_one_fet11-01_12-58-54        ripple_time_bin_marginals_df   
2    kdiba_pin01_one_fet11-01_12-58-54  ripple_simple_pf_pearson_merged_df   
3    kdiba_pin01_one_fet11-01_12-58-54                 ripple_marginals_df   
4    kdiba_pin01_one_fet11-01_12-58-54        laps_weighted_corr_merged_df   
..                                 ...                                 ...   
128                 2006-4-09_17-29-30      merged_complete_epoch_stats_df   
129                 2006-4-09_16-40-54      merged_complete_epoch_stats_df   
130                      11-03_12-3-25      merged_complete_epoch_stats_df   
131                      11-02_19-28-0      merged_complete_epoch_stats_df   
132                     11-02_17-46-44      merged_complete_epoch_stats_df   

                                                  path  \
0    K:\scratch\collected_outputs\2024-04-15_1050PM...   
1    K:\scratch\collected_outputs\2024-04-15_1050PM...   
2    K:\scratch\collected_outputs\2024-04-15_1050PM...   
3    K:\scratch\collected_outputs\2024-04-15_1050PM...   
4    K:\scratch\collected_outputs\2024-04-15_1050PM...   
..                                                 ...   
128  K:\scratch\collected_outputs\2024-04-15_GL-200...   
129  K:\scratch\collected_outputs\2024-04-15_GL-200...   
130  K:\scratch\collected_outputs\2024-04-15_GL-11-...   
131  K:\scratch\collected_outputs\2024-04-15_GL-11-...   
132  K:\scratch\collected_outputs\2024-04-15_GL-11-...   

    decoding_time_bin_size_str     export_datetime  
0                        0.025 2024-04-15 22:50:00  
1                        0.025 2024-04-15 22:50:00  
2                        0.025 2024-04-15 22:50:00  
3                        0.025 2024-04-15 22:50:00  
4                        0.025 2024-04-15 22:50:00  
..                         ...                 ...  
128                       None 2024-04-15 00:00:00  
129                       None 2024-04-15 00:00:00  
130                       None 2024-04-15 00:00:00  
131                       None 2024-04-15 00:00:00  
132                       None 2024-04-15 00:00:00  

[133 rows x 5 columns]

In [ ]:
parsed_csv_files_df['file_type'].unique()

In [ ]:
parsed_csv_files_df[parsed_csv_files_df['file_type'] == 'ripple_all_scores_merged_df']

In [ ]:
csv_sessions

### h5_files

In [5]:
## INPUTS: session_dict, cuttoff_date, known_bad_session_strs
if known_bad_session_strs is None:
    known_bad_session_strs = []

if cuttoff_date is not None:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items() if ((an_export_datetime >= cuttoff_date) and (session_str not in known_bad_session_strs))}
                                                                                              for session_str, session_dict in csv_sessions.items() }
else:
    # no cutoff recency date:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items() if (session_str not in known_bad_session_strs)}
                                                                                            for session_str, session_dict in csv_sessions.items()}


for session_str, session_dict in final_sessions.items():
    session_name = str(session_str)  # Extract session name from the filename
    if debug_print:
        print(f'processing session_name: {session_name}')
    curr_session_t_delta = t_delta_dict.get(session_name, {}).get('t_delta', None)
    if curr_session_t_delta is None:
        print(f'WARN: curr_session_t_delta is None for session_str = "{session_str}"')

    # Process each file type with its corresponding details
    _process_and_load_exported_file(session_dict, 'laps_marginals_df', final_sessions_loaded_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_marginals_df', final_sessions_loaded_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    _process_and_load_exported_file(session_dict, 'laps_time_bin_marginals_df', final_sessions_loaded_laps_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    _process_and_load_exported_file(session_dict, 'ripple_time_bin_marginals_df', final_sessions_loaded_ripple_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    _process_and_load_exported_file(session_dict, 'laps_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    _process_and_load_exported_file(session_dict, 'laps_weighted_corr_merged_df', final_sessions_loaded_laps_wcorr_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_weighted_corr_merged_df', final_sessions_loaded_ripple_wcorr_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    
    # _process_and_load_exported_file(session_dict, 'laps_all_scores_merged_df', final_sessions_loaded_laps_all_scores_dict, session_str, curr_session_t_delta, 'lap_start_t')
    _process_and_load_exported_file(session_dict, 'ripple_all_scores_merged_df', final_sessions_loaded_ripple_all_scores_dict, session_str, curr_session_t_delta, 'ripple_start_t')


parsed_h5_files_df: pd.DataFrame = convert_to_dataframe(h5_sessions)
parsed_h5_files_df

session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: laps_marginals_df - did not fully work. (error 'laps_marginals_df'. Skipping.
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: ripple_marginals_df - did not fully work. (error 'ripple_marginals_df'. Skipping.
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: laps_time_bin_marginals_df - did not fully work. (error 'laps_time_bin_marginals_df'. Skipping.
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: ripple_time_bin_marginals_df - did not fully work. (error 'ripple_time_bin_marginals_df'. Skipping.
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: laps_simple_pf_pearson_merged_df - did not fully work. (error 'laps_simple_pf_pearson_merged_df'. Skipping.
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: ripple_simple_pf_pearson_merged_df - did not fully work. (error 'ripple_simple_pf_pearson_merged_df'. Skipping.
session kdiba_pin01_one_11-02_17-46-44, df_file_name_key: laps_weighted_corr

session                    file_type  \
0    fet11-01_12-58-54  time_bin_size_sweep_results   
1    fet11-01_12-58-54             pipeline_results   
2   2006-6-12_16-53-46  time_bin_size_sweep_results   
3   2006-6-12_16-53-46             pipeline_results   
4   2006-6-12_15-55-31  time_bin_size_sweep_results   
5   2006-6-12_15-55-31             pipeline_results   
6   2006-6-09_22-24-40  time_bin_size_sweep_results   
7   2006-6-09_22-24-40             pipeline_results   
8    2006-6-09_1-22-43  time_bin_size_sweep_results   
9    2006-6-09_1-22-43             pipeline_results   
10  2006-6-08_21-16-25  time_bin_size_sweep_results   
11  2006-6-08_21-16-25             pipeline_results   
12  2006-6-08_14-26-15  time_bin_size_sweep_results   
13  2006-6-08_14-26-15             pipeline_results   
14  2006-6-07_16-40-19  time_bin_size_sweep_results   
15  2006-6-07_16-40-19             pipeline_results   
16   2006-4-10_12-58-3  time_bin_size_sweep_results   
17   2006-4-10_12-58-3             pipeline_results   
18  2006-4-10_12-25-50  time_bin_size_sweep_results   
19  2006-4-10_12-25-50             pipeline_results   
20  2006-4-09_17-29-30  time_bin_size_sweep_results   
21  2006-4-09_17-29-30             pipeline_results   
22  2006-4-09_16-40-54  time_bin_size_sweep_results   
23  2006-4-09_16-40-54             pipeline_results   
24       11-03_12-3-25  time_bin_size_sweep_results   
25       11-03_12-3-25             pipeline_results   
26       11-02_19-28-0  time_bin_size_sweep_results   
27       11-02_19-28-0             pipeline_results   
28      11-02_17-46-44  time_bin_size_sweep_results   
29      11-02_17-46-44             pipeline_results   
30               kdiba                          vvp   
31               kdiba                          pin   
32               kdiba                          gor   

                                                 path  \
0   K:\scratch\collected_outputs\2024-04-15_GL-fet...   
1   K:\scratch\collected_outputs\2024-04-15_GL_fet...   
2   K:\scratch\collected_outputs\2024-04-15_GL-200...   
3   K:\scratch\collected_outputs\2024-04-15_GL_200...   
4   K:\scratch\collected_outputs\2024-04-15_GL-200...   
5   K:\scratch\collected_outputs\2024-04-15_GL_200...   
6   K:\scratch\collected_outputs\2024-04-15_GL-200...   
7   K:\scratch\collected_outputs\2024-04-15_GL_200...   
8   K:\scratch\collected_outputs\2024-04-15_GL-200...   
9   K:\scratch\collected_outputs\2024-04-15_GL_200...   
10  K:\scratch\collected_outputs\2024-04-15_GL-200...   
11  K:\scratch\collected_outputs\2024-04-15_GL_200...   
12  K:\scratch\collected_outputs\2024-04-15_GL-200...   
13  K:\scratch\collected_outputs\2024-04-15_GL_200...   
14  K:\scratch\collected_outputs\2024-04-15_GL-200...   
15  K:\scratch\collected_outputs\2024-04-15_GL_200...   
16  K:\scratch\collected_outputs\2024-04-15_GL-200...   
17  K:\scratch\collected_outputs\2024-04-15_GL_200...   
18  K:\scratch\collected_outputs\2024-04-15_GL-200...   
19  K:\scratch\collected_outputs\2024-04-15_GL_200...   
20  K:\scratch\collected_outputs\2024-04-15_GL-200...   
21  K:\scratch\collected_outputs\2024-04-15_GL_200...   
22  K:\scratch\collected_outputs\2024-04-15_GL-200...   
23  K:\scratch\collected_outputs\2024-04-15_GL_200...   
24  K:\scratch\collected_outputs\2024-04-15_GL-11-...   
25  K:\scratch\collected_outputs\2024-04-15_GL_11-...   
26  K:\scratch\collected_outputs\2024-04-15_GL-11-...   
27  K:\scratch\collected_outputs\2024-04-15_GL_11-...   
28  K:\scratch\collected_outputs\2024-04-15_GL-11-...   
29  K:\scratch\collected_outputs\2024-04-15_GL_11-...   
30  K:\scratch\collected_outputs\2024-03-28_Apogee...   
31  K:\scratch\collected_outputs\2024-03-28_Apogee...   
32  K:\scratch\collected_outputs\2024-03-28_Apogee...   

   decoding_time_bin_size_str export_datetime  
0                        None      2024-04-15  
1                        None      2024-04-15  
2                        None      2024-04-15  
3            

In [ ]:
# 2024-03-28_Apogee_11-02_17-46-44_pipeline_results.h5

In [ ]:
h5_sessions # get 'pipeline_results' results
h5_sessions

[a_session_dict.get('pipeline_results', None)[0] for a_sess_name, a_session_dict in h5_sessions.items()]

In [6]:


h5_session_names = list(h5_sessions.keys())
h5_session_names

['fet11-01_12-58-54',
 '2006-6-12_16-53-46',
 '2006-6-12_15-55-31',
 '2006-6-09_22-24-40',
 '2006-6-09_1-22-43',
 '2006-6-08_21-16-25',
 '2006-6-08_14-26-15',
 '2006-6-07_16-40-19',
 '2006-4-10_12-58-3',
 '2006-4-10_12-25-50',
 '2006-4-09_17-29-30',
 '2006-4-09_16-40-54',
 '11-03_12-3-25',
 '11-02_19-28-0',
 '11-02_17-46-44',
 'kdiba']

In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import parse_filename




# _test_h5_filename = Path("2024-03-28_Apogee_kdiba_gor01_one_2006-6-08_14-26-15_pipeline_results.h5")
_test_h5_filename = Path("2024-03-28-Apogee_kdiba_gor01_one_2006-6-08_14-26-15_pipeline_results.h5")

parse_filename(_test_h5_filename)

In [ ]:
# _test_h5_filename = Path("2024-03-28-Apogee_kdiba_gor01_one_2006-6-08_14-26-15_pipeline_results.h5")
_test_h5_filename = Path("2024-03-28_Apogee_11-02_17-46-44_pipeline_results.h5")

basename: str = _test_h5_filename.stem
final_parsed_output_dict = try_parse_chain(basename=basename)
final_parsed_output_dict
# a_test_parser = DayDateOnlyParser()
# a_test_parser.try_parse(_test_h5_filename.stem)

In [ ]:
from pyphocorehelpers.Filesystem.path_helpers import read_filelist_from_text_file

an_h5_filelist_path = Path(r'L:/Scratch/collected_outputs/2024-03-28_Apogee_all_sessions_h5_filelist.txt').resolve()
read_hdf5_output_paths = read_filelist_from_text_file(filelist_path=an_h5_filelist_path, debug_print=False)
read_hdf5_output_paths

In [7]:
from neuropy.core.user_annotations import UserAnnotationsManager

## INPUTS: h5_sessions
h5_session_names = list(h5_sessions.keys())
good_sessions = UserAnnotationsManager.get_hardcoded_good_sessions()
h5_session_contexts = [a_good_session_ctxt for a_good_session_ctxt in good_sessions if (a_good_session_ctxt.session_name in h5_session_names)]
h5_session_contexts

# included_h5_paths = [a_session_dict.get('pipeline_results', None)[0] for a_sess_name, a_session_dict in h5_sessions.items()] # these are mis-ordered
included_h5_paths = [h5_sessions[a_good_session_ctxt.session_name].get('pipeline_results', None)[0] for a_good_session_ctxt in h5_session_contexts]
assert len(included_h5_paths) == len(h5_session_contexts)

h5_contexts_paths_dict = dict(zip(h5_session_contexts, included_h5_paths))
h5_contexts_paths_dict

{Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'one'
         session_name: '2006-6-08_14-26-15'): WindowsPath('K:/scratch/collected_outputs/2024-04-15_GL_2006-6-08_14-26-15_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'one'
         session_name: '2006-6-09_1-22-43'): WindowsPath('K:/scratch/collected_outputs/2024-04-15_GL_2006-6-09_1-22-43_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'one'
         session_name: '2006-6-12_15-55-31'): WindowsPath('K:/scratch/collected_outputs/2024-04-15_GL_2006-6-12_15-55-31_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'two'
         session_name: '2006-6-07_16-40-19'): WindowsPath('K:/scratch/collected_outputs/2024-04-15_GL_2006-6-07_16-40-19_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'two'
         session

In [8]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionTables
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsVisualizations

included_session_contexts = deepcopy(h5_session_contexts)
included_h5_paths = deepcopy(included_h5_paths)
num_sessions = len(included_session_contexts)
neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table = AcrossSessionTables.build_all_known_tables(included_session_contexts, included_h5_paths, should_restore_native_column_types=True)

# neuron_replay_stats_table = AcrossSessionTables.build_neuron_replay_stats_table(included_session_contexts, included_h5_paths)
# neuron_replay_stats_table

# long_short_fr_indicies_analysis_table = AcrossSessionTables.build_long_short_fr_indicies_analysis_table(included_session_contexts, included_h5_paths)
# long_short_fr_indicies_analysis_table

# long_short_fr_indicies_analysis_table

concatenating dataframes from 15 of 15 files
concatenating dataframes from 15 of 15 files
concatenating dataframes from 15 of 15 files


In [ ]:
neuron_replay_stats_table

In [9]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsResults

# matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')

AcrossSessionsResults.post_compute_all_sessions_processing(global_data_root_parent_path=collected_outputs_directory, BATCH_DATE_TO_USE=TODAY_DAY_DATE, plotting_enabled=True)

global_batch_result_inst_fr_file_path: K:\scratch\collected_outputs\across_session_result_long_short_recomputed_inst_firing_rate_2024-04-16_APOGEE.pkl
Loading loaded session pickle file results : K:\scratch\collected_outputs\across_session_result_long_short_recomputed_inst_firing_rate_2024-04-16_APOGEE.pkl... done.


FileNotFoundError: [Errno 2] No such file or directory: 'K:\\scratch\\collected_outputs\\across_session_result_long_short_recomputed_inst_firing_rate_2024-04-16_APOGEE.pkl'

In [ ]:
global_multi_session_context, _out_aggregate_fig_2 = AcrossSessionsVisualizations.across_sessions_bar_graphs(across_session_inst_fr_computation, num_sessions, enable_tiny_point_labels=False, enable_hover_labels=False)

In [ ]:
graphics_output_dict = AcrossSessionsVisualizations.across_sessions_firing_rate_index_figure(long_short_fr_indicies_analysis_results=long_short_fr_indicies_analysis_table, num_sessions=num_sessions)

In [ ]:
print(list(all_sessions_all_scores_ripple_df.columns)) # ['start', 'stop', 'label', 'duration', 'is_user_annotated_epoch', 'is_valid_epoch', 'P_LR', 'P_RL', 'P_Long', 'P_Short', 'P_Long_LR', 'score_long_LR', 'velocity_long_LR', 'intercept_long_LR', 'speed_long_LR', 'wcorr_long_LR', 'pearsonr_long_LR', 'travel_long_LR', 'coverage_long_LR', 'jump_long_LR', 'longest_sequence_length_ratio_long_LR', 'direction_change_bin_ratio_long_LR', 'congruent_dir_bins_ratio_long_LR', 'total_congruent_direction_change_long_LR', 'P_Long_RL', 'score_long_RL', 'velocity_long_RL', 'intercept_long_RL', 'speed_long_RL', 'wcorr_long_RL', 'pearsonr_long_RL', 'travel_long_RL', 'coverage_long_RL', 'jump_long_RL', 'longest_sequence_length_ratio_long_RL', 'direction_change_bin_ratio_long_RL', 'congruent_dir_bins_ratio_long_RL', 'total_congruent_direction_change_long_RL', 'P_Short_LR', 'score_short_LR', 'velocity_short_LR', 'intercept_short_LR', 'speed_short_LR', 'wcorr_short_LR', 'pearsonr_short_LR', 'travel_short_LR', 'coverage_short_LR', 'jump_short_LR', 'longest_sequence_length_ratio_short_LR', 'direction_change_bin_ratio_short_LR', 'congruent_dir_bins_ratio_short_LR', 'total_congruent_direction_change_short_LR', 'P_Short_RL', 'score_short_RL', 'velocity_short_RL', 'intercept_short_RL', 'speed_short_RL', 'wcorr_short_RL', 'pearsonr_short_RL', 'travel_short_RL', 'coverage_short_RL', 'jump_short_RL', 'longest_sequence_length_ratio_short_RL', 'direction_change_bin_ratio_short_RL', 'congruent_dir_bins_ratio_short_RL', 'total_congruent_direction_change_short_RL', 'ripple_start_t', 'long_best_travel', 'short_best_travel', 'travel_diff', 'long_best_coverage', 'short_best_coverage', 'coverage_diff', 'long_best_jump', 'short_best_jump', 'jump_diff', 'long_best_longest_sequence_length_ratio', 'short_best_longest_sequence_length_ratio', 'longest_sequence_length_ratio_diff', 'long_best_direction_change_bin_ratio', 'short_best_direction_change_bin_ratio', 'direction_change_bin_ratio_diff', 'long_best_congruent_dir_bins_ratio', 'short_best_congruent_dir_bins_ratio', 'congruent_dir_bins_ratio_diff', 'long_best_total_congruent_direction_change', 'short_best_total_congruent_direction_change', 'total_congruent_direction_change_diff', 'session_name', 'time_bin_size', 'delta_aligned_start_t']
# ['long_best_total_congruent_direction_change', 'short_best_total_congruent_direction_change']
['longest_sequence_length_ratio_diff', 'direction_change_bin_ratio_diff', 'congruent_dir_bins_ratio_diff', 'total_congruent_direction_change_diff']

In [ ]:
all_sessions_simple_pearson_ripple_df # 3138 rows × 24 columns

In [ ]:
all_sessions_simple_pearson_laps_df # 931 rows × 25 columns

In [ ]:
all_sessions_ripple_df # 17592 rows × 10 columns

In [ ]:
csv_files

In [3]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import export_across_session_CSVs

# TODAY_DAY_DATE: str = f"2024-03-18_Apogee"
final_output_path = Path("../output/").resolve()

final_csv_export_paths = export_across_session_CSVs(final_output_path=final_output_path, TODAY_DAY_DATE=TODAY_DAY_DATE,
                                                    all_sessions_laps_df=all_sessions_laps_df,  all_sessions_ripple_df=all_sessions_ripple_df,  all_sessions_laps_time_bin_df=all_sessions_laps_time_bin_df,  all_sessions_ripple_time_bin_df=all_sessions_ripple_time_bin_df, 
                                                    all_sessions_simple_pearson_laps_df=all_sessions_simple_pearson_laps_df,  all_sessions_simple_pearson_ripple_df=all_sessions_simple_pearson_ripple_df,
                                                    all_sessions_all_scores_ripple_df=all_sessions_all_scores_ripple_df,  all_sessions_all_scores_laps_df=None,
                                                    )
final_csv_export_paths

{'AcrossSession_Laps_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-16_APOGEE_AcrossSession_Laps_per-Epoch.csv'),
 'AcrossSession_Ripple_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-16_APOGEE_AcrossSession_Ripple_per-Epoch.csv'),
 'AcrossSession_Laps_per-TimeBin': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-16_APOGEE_AcrossSession_Laps_per-TimeBin.csv'),
 'AcrossSession_Ripple_per-TimeBin': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-16_APOGEE_AcrossSession_Ripple_per-TimeBin.csv'),
 'AcrossSession_SimplePearson_Laps_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-16_APOGEE_AcrossSession_SimplePearson_Laps_per-Epoch.csv'),
 'AcrossSession_SimplePearson_Ripple_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-16_APOGEE_AcrossSession_SimplePearson_Ripple_per-Epoch.csv'),
 'AcrossSession_AllScores_Ripp

In [ ]:
all_sessions_all_scores_ripple_df

In [10]:

all_sessions_simple_pearson_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0     4.560041e-01  0.543996  0.493835  0.506165           0        1.489151   
1     5.734207e-01  0.426579  0.631624  0.368376           1        3.490896   
2     5.087652e-01  0.491235  0.549421  0.450579           2       12.982910   
3     5.476339e-01  0.452366  0.521215  0.478785           3       46.106580   
4     4.882640e-01  0.511736  0.697056  0.302944           4       53.350137   
...            ...       ...       ...       ...         ...             ...   
3945  2.263085e-01  0.773692  0.301660  0.698340         407     1731.111480   
3946  7.050154e-07  0.999999  0.580727  0.419273         408     1731.789992   
3947  5.131128e-01  0.486887  0.320867  0.679133         409     1733.729959   
3948  3.099668e-01  0.690033  0.304357  0.695643         410     1734.961032   
3949  4.793921e-01  0.520608  0.718233  0.281767         411     1736.892796   

         P_Long_LR  P_Long_RL    P_Short_LR  P_Short_RL  \
0     2.251908e-01   0.268644  2.308133e-01    0.275352   
1     3.621860e-01   0.269438  2.112347e-01    0.157142   
2     2.795263e-01   0.269895  2.292389e-01    0.221340   
3     2.854353e-01   0.235780  2.621986e-01    0.216586   
4     3.403474e-01   0.356709  1.479166e-01    0.155027   
...            ...        ...           ...         ...   
3945  6.826824e-02   0.233392  1.580403e-01    0.540300   
3946  4.094216e-07   0.580727  2.955938e-07    0.419272   
3947  1.646410e-01   0.156226  3.484718e-01    0.330661   
3948  9.434053e-02   0.210016  2.156263e-01    0.480017   
3949  3.443152e-01   0.373918  1.350768e-01    0.146690   

      most_likely_decoder_index        start         stop  label  duration  \
0                             3     1.489151     1.924423      0  0.435271   
1                             0     3.490896     4.041767      1  0.550871   
2                             0    12.982910    13.469085      3  0.486174   
3                             0    46.106580    46.596564     12  0.489984   
4                             1    53.350137    53.520510     14  0.170373   
...                         ...          ...          ...    ...       ...   
3945                          3  1731.111480  1731.287905    418  0.176425   
3946                          1  1731.789992  1731.848606    419  0.058614   
3947                          2  1733.729959  1733.857078    420  0.127119   
3948                          3  1734.961032  1735.034760    421  0.073728   
3949                          1  1736.892796  1736.958814    422  0.066017   

      long_LR_pf_peak_x_pearsonr  long_RL_pf_peak_x_pearsonr  \
0                      -0.092771                    0.048261   
1                      -0.250747                   -0.061340   
2                            NaN                         NaN   
3                      -0.700175                    0.079102   
4                            NaN                         NaN   
...                          ...                         ...   
3945                         NaN                         NaN   
3946                         NaN                         NaN   
3947                    0.062284                   -0.016317   
3948                         NaN                         NaN   
3949                         NaN                         NaN   

      short_LR_pf_peak_x_pearsonr  short_RL_pf_peak_x_pearsonr  \
0                       -0.148103                    -0.056006   
1                       -0.298784                     0.047536   
2                             NaN                          NaN   
3                       -0.235632                    -0.126138   
4                             NaN                          NaN   
...                           ...                          ...   
3945                          NaN                          NaN   
3946                          NaN                          NaN   
3947                     0.242668           

In [ ]:
## find all columns starting with 'wcorr': wcorr_long_LR
sub_string: str = 'wcorr'
sub_string: str = 'pearsonr'
columns_list = list(all_sessions_simple_pearson_ripple_df.columns)
matching_columns = [s for s in columns_list if sub_string in s]
print(matching_columns) # ['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']
['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

assert np.shape(all_sessions_simple_pearson_ripple_df)[0] == np.shape(all_sessions_all_scores_ripple_df)[0], f"np.shape(all_sessions_all_scores_ripple_df)[0]: {np.shape(all_sessions_all_scores_ripple_df)[0]} != np.shape(all_sessions_simple_pearson_ripple_df)[0]: {np.shape(all_sessions_simple_pearson_ripple_df)[0]}"



In [ ]:
['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']
['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

# 2024-03-02 - Get only the user-annotated ripples:

In [4]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _split_user_annotated_ripple_df

## Bump
# input_df = all_sessions_simple_pearson_ripple_df
# input_df = all_sessions_all_scores_ripple_df

all_sessions_all_scores_ripple_df, (valid_ripple_df, invalid_ripple_df), (user_approved_ripple_df, user_rejected_ripple_df) = _split_user_annotated_ripple_df(all_sessions_all_scores_ripple_df)

## 2024-03-14 - 'is_valid_epoch' column
# 'is_valid_epoch'
## OUTPUTS: valid_ripple_df, invalid_ripple_df, user_approved_ripple_df, user_rejected_ripple_df, (user_annotated_epoch_unique_session_names, unannotated_session_names)
user_approved_ripple_df

user_annotated_epoch_unique_session_names: ['kdiba_pin01_one_fet11-01_12-58-54' 'kdiba_pin01_one_11-02_19-28-0'
 'kdiba_gor01_two_2006-6-09_22-24-40' 'kdiba_gor01_one_2006-6-12_15-55-31'
 'kdiba_gor01_one_2006-6-09_1-22-43']
unannotated_session_names: set()
n_input_df_rows: 2138
	 n_valid_df_rows: 1255
	 n_invalid_df_rows: 883
n_input_df_rows: 1255
	 n_user_approved_df_rows: 187
	 n_user_rejected_df_rows: 1068


start         stop  label  duration      P_LR      P_RL    P_Long  \
0      72.773154    72.958611     28  0.185457  0.610744  0.389256  0.807523   
1     127.406680   127.814365     50  0.407685  0.436479  0.563521  0.651931   
2     135.956513   136.408127     52  0.451614  0.500617  0.499383  0.687366   
3     248.042369   248.455430     86  0.413061  0.508420  0.491580  0.532468   
4     403.414434   403.817972    123  0.403538  0.512006  0.487994  0.562196   
..           ...          ...    ...       ...       ...       ...       ...   
182  1699.225242  1699.356969    403  0.131727  0.430035  0.569965  0.051056   
183  1705.053099  1705.140866    405  0.087767  0.999975  0.000025  0.021224   
184  1707.712068  1707.918998    406  0.206930  0.524099  0.475901  0.228705   
185  1725.278891  1725.595092    414  0.316201  0.329744  0.670256  0.428396   
186  1731.111480  1731.287905    418  0.176425  0.226308  0.773692  0.301660   

      P_Short  P_Long_LR  score_long_LR  velocity_long_LR  intercept_long_LR  \
0    0.192477   0.493190       0.430106       -235.189189          57.973200   
1    0.348069   0.284555       0.247489        133.456144         165.439477   
2    0.312634   0.344107       0.322034         30.735418         190.887113   
3    0.467532   0.270717       0.288624         14.186461          33.682970   
4    0.437804   0.287848       0.304061       -542.605505         205.148298   
..        ...        ...            ...               ...                ...   
182  0.948944   0.021956       0.530856       -414.658521         215.636352   
183  0.978776   0.021224       0.855817      -2077.470241         163.664238   
184  0.771295   0.119864       0.540374          9.469654         199.625365   
185  0.571604   0.141261       0.425058       -672.876530         216.519650   
186  0.698340   0.068268       0.416600       -133.151447         130.418937   

     speed_long_LR  wcorr_long_LR  pearsonr_long_LR  travel_long_LR  \
0       235.189189       0.336037               NaN        0.554423   
1       133.456144       0.282668          0.574375        0.282146   
2        30.735418       0.239263          0.643636        0.377014   
3        14.186461      -0.015162          0.461667        0.143976   
4       542.605505      -0.141540               NaN        0.228736   
..             ...            ...               ...             ...   
182     414.658521      -0.676474          0.444107        0.195606   
183    2077.470241      -0.951116               NaN        0.164486   
184       9.469654      -0.505128               NaN        0.210155   
185     672.876530      -0.578459         -0.297006        0.168932   
186     133.151447      -0.279661               NaN        0.220501   

     coverage_long_LR  jump_long_LR  longest_sequence_length_ratio_long_LR  \
0            0.444444      0.003995                               0.285714   
1            0.365079      0.004145                               0.312500   
2            0.301587      0.004145                               0.222222   
3            0.301587      0.003618                               0.437500   
4            0.492063      0.004145                               0.250000   
..                ...           ...                                    ...   
182          0.280702      0.003588                               0.250000   
183          0.403509      0.001001                               0.800000   
184          0.228070      0.002754                               0.083333   
185          0.315789      0.002921                               0.157895   
186          0.263158      0.004673                               0.272727   

     direction_change_bin_ratio_long_LR  congruent_dir_bins_ratio_long_LR  \
0                              0.833333                          0.333333   
1                              0.533333                          0.533333   
2                              0.647059                          0.5

In [ ]:
user_approved_ripple_df

In [ ]:
[col.split('_long_LR') for col in list(user_approved_ripple_df.columns)]



In [ ]:
## order columns for reasonability
['long_best_coverage', 'short_best_coverage', 'coverage_diff']

['coverage_short_RL']

['_long_LR', '_long_RL', '_short_LR', '_short_RL']
['long_best_', 'short_best_']
['_diff']


# PandasHelpers.reordering_columns(


In [ ]:
## want to compare difference between user approved and user rejected ripples

user_approved_ripple_df
user_rejected_ripple_df
# OUTPUTS: all_sessions_user_annotated_ripple_df, user_approved_ripple_df, user_rejected_ripple_df

In [ ]:
## Want to test for differences between long/short among only user approved ripples:

0.025


In [ ]:
df: pd.DataFrame = deepcopy(all_sessions_user_annotated_ripple_df)

### 2024-02-29 - 4pm - Filter the events for those meeting wcorr criteria:


In [ ]:
# df: pd.DataFrame = deepcopy(all_sessions_user_annotated_ripple_df)
df: pd.DataFrame = deepcopy(valid_ripple_df) # valid epochs, but not just those that the user approved
# df: pd.DataFrame = deepcopy(user_approved_ripple_df)

## INPUTS: df

min_wcorr_threshold: float = 0.33
min_wcorr_diff_threshold: float = 0.2

# is_included_large_wcorr_diff = np.any((df[['wcorr_abs_diff']].abs() > min_wcorr_diff_threshold), axis=1)
is_included_large_wcorr_diff = np.any((df[['wcorr_diff']].abs() > min_wcorr_diff_threshold), axis=1)
is_included_high_wcorr = np.any((df[['long_best_wcorr', 'short_best_wcorr']].abs() > min_wcorr_threshold), axis=1)

df = df[is_included_high_wcorr]
df

# wcorr_long_LR


# Plotting via Plotly

In [11]:
import plotly.io as pio
template: str = 'plotly_dark' # set plotl template
# template: str = 'plotly_white'
pio.templates.default = template
from PIL import Image

from pyphocorehelpers.programming_helpers import copy_image_to_clipboard
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _helper_build_figure, plotly_pre_post_delta_scatter, plot_across_sessions_scatter_results

# 1650, 446
fig_size_kwargs = {'width': 1650, 'height': 480}

In [12]:
## INPUTS: all_sessions_all_scores_ripple_df
concatenated_ripple_df = deepcopy(all_sessions_all_scores_ripple_df).infer_objects()

## Add plotly helper columns:
concatenated_ripple_df['pre_post_delta_category'] = 'post-delta'
concatenated_ripple_df['pre_post_delta_category'][concatenated_ripple_df['delta_aligned_start_t'] < 0.0] = 'pre-delta'


{'pre_post_delta_category': ['pre-delta', 'post-delta']
}

ripple_title_prefix = "User Annotated Sessions Ripples"

# concatenated_ripple_df = deepcopy(user_approved_ripple_df)
# ripple_title_prefix = "User Selected Ripples Only"

# concatenated_ripple_df = deepcopy(user_rejected_ripple_df)
# ripple_title_prefix = "User Rejected Ripples Only"

# concatenated_ripple_df = deepcopy(df)


# Create a bubble chart for ripples
enabled_time_bin_sizes = None
ripple_num_unique_sessions: int = concatenated_ripple_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
ripple_num_unique_time_bins: int = concatenated_ripple_df.time_bin_size.nunique(dropna=True)
ripple_title_string_suffix: str = f'{ripple_num_unique_sessions} Sessions'
ripple_title: str = f"{ripple_title_prefix} - {ripple_title_string_suffix}"
fig_ripples, figure_ripples_context = _helper_build_figure(data_results_df=concatenated_ripple_df, histogram_bins=25, earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end, enabled_time_bin_sizes=enabled_time_bin_sizes, main_plot_mode='default', title=ripple_title)
fig_ripples = fig_ripples.update_layout(fig_size_kwargs)
fig_ripples.show()
# fig_to_clipboard(fig_ripples)

num_unique_sessions: 5, num_unique_time_bins: 1
main_plot_mode: default
num_cols: 2


C:\Users\pho\AppData\Local\Temp\ipykernel_150728\459722990.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  concatenated_ripple_df['pre_post_delta_category'][concatenated_ripple_df['delta_aligned_start_t'] < 0.0] = 'pre-delta'


In [ ]:
## TODAY_DAY_DATE:str, figure_ripples_context
fig_save_path: Path = figures_folder.joinpath('_'.join([TODAY_DAY_DATE, figure_ripples_context.get_description()])).resolve()
figure_out_paths = {'.html': fig_save_path.with_suffix('.html'), '.png': fig_save_path.with_suffix('.png')}
fig_ripples.write_html(figure_out_paths['.html'])
print(file_uri_from_path(figure_out_paths['.html']))
fig_ripples.write_image(figure_out_paths['.png'])
print(file_uri_from_path(figure_out_paths['.png']))



In [13]:
histogram_bins = 25
# concatenated_ripple_df = deepcopy(df)

# ripple_title_prefix = 'test'
# # Create a bubble chart for ripples
# ripple_num_unique_sessions: int = concatenated_ripple_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
# # ripple_num_unique_time_bins: int = concatenated_ripple_df.time_bin_size.nunique(dropna=True)
# ripple_title_string_suffix: str = f'{ripple_num_unique_sessions} Sessions'
# ripple_title: str = f"{ripple_title_prefix} - {ripple_title_string_suffix}"
# fig_ripples = _helper_build_figure(data_results_df=concatenated_ripple_df, histogram_bins=histogram_bins, earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end, enabled_time_bin_sizes=None,
#                                     main_plot_mode='separate_row_per_session', title=ripple_title)

# concatenated_ripple_df = deepcopy(concatenated_ripple_df)
concatenated_ripple_df = deepcopy(all_sessions_all_scores_ripple_df)

# ['longest_sequence_length_ratio_diff', 'direction_change_bin_ratio_diff', 'congruent_dir_bins_ratio_diff', 'total_congruent_direction_change_diff']


# variable_name = 'P_Long'
variable_name = 'P_Short' # Shows expected effect - short-only replay prior to delta and then split replays post-delta
# variable_name = 'long_best_pf_peak_x_pearsonr'
# variable_name = 'long_best_jump'
# variable_name = 'wcorr_abs_diff'
# variable_name = 'pearsonr_abs_diff'
# variable_name = 'direction_change_bin_ratio_diff'
# variable_name = 'longest_sequence_length_ratio_diff'
# variable_name = 'long_best_longest_sequence_length_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'congruent_dir_bins_ratio_diff'
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
new_fig_ripples, new_fig_ripples_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples = new_fig_ripples.update_layout(fig_size_kwargs)

_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')

# fig_to_clipboard(new_fig_ripples, **fig_size_kwargs)
new_fig_ripples

num_unique_sessions: 5, num_unique_time_bins: 1
len(pre_delta_fig.data): 2


In [ ]:
## TODAY_DAY_DATE:str, figure_ripples_context, new_fig_ripples
fig_save_path: Path = figures_folder.joinpath('_'.join([TODAY_DAY_DATE, figure_ripples_context.get_description()])).resolve()
figure_out_paths = {'.html': fig_save_path.with_suffix('.html'), '.png': fig_save_path.with_suffix('.png')}
new_fig_ripples.write_html(figure_out_paths['.html'])
print(file_uri_from_path(figure_out_paths['.html']))
new_fig_ripples.write_image(figure_out_paths['.png'])
print(file_uri_from_path(figure_out_paths['.png']))

In [ ]:
# new_fig_ripples.get_subplot(
# import kaleido

# new_fig_ripples.layout
new_fig_ripples.layout.width

# from kaleido._version import __version__ # '0.1.0.post1'
# __version__

color_options = ["is_user_annotated_epoch", "pre_post_delta_category"]

variable_options = {'pre_post_delta_category': ['pre-delta', 'post-delta']
}

concatenated_ripple_df

In [ ]:
variable_name = 'short_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'short_best_wcorr'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"pre_post_delta_category", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], , 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="pre_post_delta_category") # , histnorm='probability density'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.0, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples

In [ ]:
## TODAY_DAY_DATE:str, figure_context, new_fig_ripples
fig_save_path: Path = figures_folder.joinpath('_'.join([TODAY_DAY_DATE, figure_context.get_description()])).resolve()
new_fig_ripples.write_html(fig_save_path.with_suffix('.html'))
new_fig_ripples.write_image(fig_save_path.with_suffix('.png'))

In [ ]:
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_total_congruent_direction_change'
variable_name = 'wcorr_diff'
# variable_name = 'long_best_wcorr'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'", 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.0, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples

In [ ]:
## TODAY_DAY_DATE:str, figure_context, new_fig_ripples
fig_save_path: Path = figures_folder.joinpath('_'.join([TODAY_DAY_DATE, figure_context.get_description()])).resolve()
new_fig_ripples.write_html(fig_save_path.with_suffix('.html'))
new_fig_ripples.write_image(fig_save_path.with_suffix('.png'))

## Stats Tests

In [ ]:
from pyphocorehelpers.indexing_helpers import partition, partition_df, partition_df_dict
import scipy.stats as stats

# stats_variable_name: str = 'P_Short'
# stats_variable_name: str = 'short_best_direction_change_bin_ratio'
stats_variable_name: str = 'short_best_wcorr'

## INPUTS: stats_variable_name, valid_ripple_df


# ['pre-delta', 'post-delta']
analysis_df = deepcopy(valid_ripple_df[["delta_aligned_start_t", "pre_post_delta_category", stats_variable_name]]).dropna(subset=["pre_post_delta_category", stats_variable_name])
# partition_df(analysis_df, partitionColumn='pre_post_delta_category')

# _partition_values, (_pre_delta_df, _post_delta_df) = partition(analysis_df, partitionColumn='pre_post_delta_category') # use `valid_ripple_df` instead of the original dataframe to only get those which are valid.
_pre_post_delta_partition_df_dict = partition_df_dict(analysis_df, partitionColumn='pre_post_delta_category')
_pre_delta_df = _pre_post_delta_partition_df_dict['pre-delta']
_post_delta_df = _pre_post_delta_partition_df_dict['post-delta']

actual_diff_means = np.nanmean(_post_delta_df[stats_variable_name].to_numpy()) - np.nanmean(_pre_delta_df[stats_variable_name].to_numpy())
print(f'stats_variable_name: {stats_variable_name}: actual_diff_means: {actual_diff_means}')

_pre_delta_df
_post_delta_df

In [ ]:
n_shuffles: int = 10000
# stats_variable_name: str = 'P_Short'

shuffle_results = []
## INPUT: n_shuffles, analysis_df, stats_variable_name
shuffled_analysis_df = deepcopy(analysis_df)
for i in np.arange(n_shuffles):
    # shuffled_analysis_df[stats_variable_name] = shuffled_analysis_df[stats_variable_name].sample(frac=1).to_numpy() # .reset_index(drop=True)
    shuffled_analysis_df['pre_post_delta_category'] = shuffled_analysis_df.sample(frac=1)['pre_post_delta_category'].to_numpy()
    _shuffled_pre_post_delta_partition_df_dict = partition_df_dict(shuffled_analysis_df, partitionColumn='pre_post_delta_category')
    _shuffled_pre_delta_df = _shuffled_pre_post_delta_partition_df_dict['pre-delta']
    _shuffled_post_delta_df = _shuffled_pre_post_delta_partition_df_dict['post-delta']

    _diff_mean = np.nanmean(_shuffled_post_delta_df[stats_variable_name].to_numpy()) - np.nanmean(_shuffled_pre_delta_df[stats_variable_name].to_numpy())
    shuffle_results.append(_diff_mean)

shuffle_results = np.array(shuffle_results)
shuffle_results

In [ ]:
np.sum(actual_diff_means > np.abs(shuffle_results))

In [ ]:
# Create the data for two groups
# group1 = np.random.rand(25)
# group2 = np.random.rand(20)

## INPUTS: stats_variable_name
print(f'stats_variable_name: {stats_variable_name}')

group1 = _pre_delta_df[stats_variable_name].to_numpy()
group2 = _post_delta_df[stats_variable_name].to_numpy()

# perform mann whitney test 
stat, p_value = stats.mannwhitneyu(group1, group2) 
print('Statistics=%.2f, p=%.2f' % (stat, p_value)) 

# Level of significance 
alpha = 0.05
# conclusion 
if p_value < alpha: 
    print('Reject Null Hypothesis (Significant difference between two samples)') 
else: 
    print('Do not Reject Null Hypothesis (No significant difference between two samples)')

# Calculate the sample variances
variance1 = np.var(group1, ddof=1)
variance2 = np.var(group2, ddof=1)
 
print('Variance 1:',variance1)
print('Variance 2:',variance2)

# Calculate the F-statistic
f_value = variance1 / variance2
 
# Calculate the degrees of freedom
df1 = len(group1) - 1
df2 = len(group2) - 1
 
# Calculate the p-value
p_value = stats.f.cdf(f_value, df1, df2)
 
# Print the results
print('Degree of freedom 1:',df1)
print('Degree of freedom 2:',df2)
print("F-statistic:", f_value)
print("p-value:", p_value)


# Statistics=351933.00, p=0.00
# Reject Null Hypothesis (Significant difference between two samples)
# Variance 1: 0.017720245875104713
# Variance 2: 0.02501347759017487
# Degree of freedom 1: 1104
# Degree of freedom 2: 1282
# F-statistic: 0.7084279189577826
# p-value: 1.882791591520268e-09


# stats_variable_name: short_best_wcorr
# Statistics=770405.00, p=0.00
# Reject Null Hypothesis (Significant difference between two samples)
# Variance 1: 0.13962063046395118
# Variance 2: 0.15575146845969287
# Degree of freedom 1: 1108
# Degree of freedom 2: 1281
# F-statistic: 0.8964321931904211
# p-value: 0.030077963036698012

In [ ]:
## User non-selected:
scatter_title = f'user_approved_ripple_df Several Sessions {variable_name}'
# variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} # , 'color': 'time_bin_size'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(user_approved_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples

In [ ]:
# IDEA: The ones with clear replays (diagonal sequences in the decoded posteriors) are by definiition ambiguous, because there's not much difference between the long/short decoders.


In [ ]:
## User non-selected:
scatter_title = f'Non-selected Several Sessions {variable_name}'
# variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} # , 'color': 'time_bin_size'
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(user_rejected_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


In [18]:
# Laps test
concatenated_ripple_df = deepcopy(all_sessions_simple_pearson_laps_df)

scatter_title = 'Several Sessions'
variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} 
new_fig_ripples, figure_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(concatenated_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


num_unique_sessions: 12, num_unique_time_bins: 1
len(pre_delta_fig.data): 1


# Plotting functions

In [14]:
from pyphoplacecellanalysis.General.Model.Configs.LongShortDisplayConfig import PlottingHelpers
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import plot_across_sessions_scatter_results

# Example usage:
all_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_df, concatenated_ripple_df=all_sessions_ripple_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   laps_title_prefix=f"Laps", ripple_title_prefix=f"Ripples", save_figures=True, figure_save_extension=['.html','.png'])
fig_laps, fig_ripples = all_session_figures[0]
# fig_laps.update_layout(fig_size_kwargs)
# fig_ripples.update_layout(fig_size_kwargs)

# fig_laps.show()
fig_ripples.show()
# fig_laps.write_html(f"../output/{TODAY_DAY_DATE}_AcrossSession_fig_laps.html")
# fig_ripples.write_html(f"../output/{TODAY_DAY_DATE}_AcrossSession_fig_ripples.html")

plot_across_sessions_results(directory: K:\scratch\collected_outputs)
	figures_folder: file:///K:/scratch/collected_outputs/figures
num_unique_sessions: 14, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
num_unique_sessions: 14, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
	saving figures...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_laps_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_ripples_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_laps_marginal.png"...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_ripples_marginal.png"...


In [ ]:
fig_to_clipboard(fig_ripples)

In [15]:
## time_bin version:
all_time_bin_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_time_bin_df, concatenated_ripple_df=all_sessions_ripple_time_bin_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   main_plot_mode='separate_row_per_session',
														   laps_title_prefix=f"Laps_per_time_bin", ripple_title_prefix=f"Ripples_per_time_bin", save_figures=True, figure_save_extension=['.html','.png'])
fig_time_bin_laps, fig_time_bin_ripples = all_time_bin_session_figures[0]
# fig_time_bin_laps.show()
fig_time_bin_ripples.show()

plot_across_sessions_results(directory: K:\scratch\collected_outputs)
	figures_folder: file:///K:/scratch/collected_outputs/figures
num_unique_sessions: 14, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
num_unique_sessions: 14, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
	saving figures...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_laps_per_time_bin_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_ripples_per_time_bin_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_laps_per_time_bin_marginal.png"...
	saving "file:///K:/scratch/collected_outputs/figures/14-Sessions_ripples_per_time_bin_marginal.png"...


In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import plotly_pre_post_delta_scatter

## Test collapsed histograms-only results:
histograms_only_all_time_bin_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_time_bin_df, concatenated_ripple_df=all_sessions_ripple_time_bin_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
															# enabled_time_bin_sizes=[0.03, 0.058, 0.10], # [0.03 , 0.044, 0.058, 0.072, 0.086, 0.1]
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   main_plot_mode='default',
														   laps_title_prefix=f"Laps_per_time_bin", ripple_title_prefix=f"Ripples_per_time_bin", save_figures=False, figure_save_extension=['.html','.png'])
histograms_only_fig_time_bin_laps, histograms_only_fig_time_bin_ripples = histograms_only_all_time_bin_session_figures[0]
# histograms_only_fig_time_bin_laps.show()
histograms_only_fig_time_bin_ripples.show()

In [ ]:
import plotly.subplots as sp
import plotly.graph_objs as go

from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import plotly_pre_post_delta_scatter
# data_results_df: pd.DataFrame = deepcopy(all_sessions_laps_df) # all_sessions_laps_time_bin_df
# histogram_bins = 'auto'
histogram_bins: int = 25

new_laps_fig, new_laps_fig_context = plotly_pre_post_delta_scatter(data_results_df=deepcopy(all_sessions_laps_df), out_scatter_fig=fig_laps, histogram_bins=histogram_bins)
new_laps_fig

# Matplotlib-based versions:

In [16]:
from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import plot_histograms

matplotlib.use('Qt5Agg')

In [ ]:
# from Spike3D.PendingNotebookCode import plot_stacked_histograms

# You can use it like this:'long_best_dir_simple_pearsonr'
_out0: "MatplotlibRenderPlots" = plot_histograms(data_type='Laps', session_spec='All Sessions', data_results_df=all_sessions_laps_time_bin_df, time_bin_duration_str="75 ms")
_out1: "MatplotlibRenderPlots" = plot_histograms(data_type='Ripples', session_spec='All Sessions', data_results_df=all_sessions_ripple_time_bin_df, time_bin_duration_str="75 ms")

In [ ]:


fig_to_clipboard(_out0.figures[0])

In [ ]:
## all_sessions_new_laps_df, all_sessions_new_ripple_df
_out0: "MatplotlibRenderPlots" = plot_histograms(data_type='New Laps', session_spec='All Sessions', data_results_df=all_sessions_new_laps_df, time_bin_duration_str="25 ms")
_out1: "MatplotlibRenderPlots" = plot_histograms(data_type='New Ripples', session_spec='All Sessions', data_results_df=all_sessions_new_ripple_df, time_bin_duration_str="25 ms")



In [ ]:
all_sessions_new_laps_df

In [ ]:
len(all_sessions_new_laps_df['session_name'].unique()) # 10 sessions



In [17]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import plot_stacked_histograms

matplotlib.use('Qt5Agg')

# You can use it like this:
num_unique_sessions: int = all_sessions_laps_time_bin_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
num_unique_time_bins: int = all_sessions_laps_time_bin_df.time_bin_size.nunique(dropna=True)
_laps_histogram_out = plot_stacked_histograms(all_sessions_laps_time_bin_df, 'Laps', f'{num_unique_sessions} Sessions', f"{num_unique_time_bins} tbin sizes")

num_unique_sessions: int = all_sessions_ripple_time_bin_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
num_unique_time_bins: int = all_sessions_ripple_time_bin_df.time_bin_size.nunique(dropna=True)
_ripple_histogram_out = plot_stacked_histograms(all_sessions_ripple_time_bin_df, 'Ripples', f'{num_unique_sessions} Sessions', f"{num_unique_time_bins} tbin sizes")

In [ ]:
_laps_histogram_out.figures[0]

figures_folder

figures_folder

# 2024-03-28 - AcrossSessionTable (PhoDibaPaper2023 formats) .h5 and figure exports

In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionTables
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsVisualizations

neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table = AcrossSessionTables.build_all_known_tables(included_session_contexts, included_h5_paths, should_restore_native_column_types=True)
num_sessions: int = len(long_short_fr_indicies_analysis_table['session_uid'].unique())
print(f'num_sessions: {num_sessions}')

long_short_fr_indicies_analysis_table

In [ ]:
# matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
matplotlib.use('Qt5Agg')
graphics_output_dict = AcrossSessionsVisualizations.across_sessions_firing_rate_index_figure(long_short_fr_indicies_analysis_results=long_short_fr_indicies_analysis_table, num_sessions=num_sessions)